¿Es posible realizar predicciones sobre el destino de un cliente utilizando variables predictoras como el tiempo, el lugar de partida, la edad y el identificador del cliente?

En esta notebook exploramos distintos clasificadores asi como variaciones de los mismos para ver el proder predictivo que se tiene para identificar donde un usuario terminara basado en la informacion que tenemos al inicio de su viaje.

# Librerias

In [1]:
# Useful
import pandas as pd
import datetime
import numpy as np
# Data helpers
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.compose import ColumnTransformer
from sklearn.metrics import confusion_matrix
# Classifiers
from sklearn.neural_network import MLPClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis
from sklearn.naive_bayes import GaussianNB
# Clustering
from sklearn.cluster import AgglomerativeClustering
# Ploting
import plotly.graph_objects as go
import plotly.express as px

# Dataset

Vamos a preparar nuestros datos para poder ser usados por los distintos clasificadores que nos proporciona Sklearn.

In [2]:
BiciDF = pd.read_csv("../data/datos_abiertos_2023_03.csv", encoding = 'latin-1')

# Parse String to Datatime
BiciDF["Inicio_del_viaje"] = pd.to_datetime(BiciDF["Inicio_del_viaje"],
               format='%Y-%m-%d %H:%M:%S')
BiciDF["Fin_del_viaje"] = pd.to_datetime(BiciDF["Fin_del_viaje"],
               format='%Y-%m-%d %H:%M:%S')

# Make the year a int instead of float
BiciDF = BiciDF.dropna()
BiciDF["Anio_de_nacimiento"] = BiciDF["Anio_de_nacimiento"].astype(int)

BiciDF.head()

Viaje_Id  Usuario_Id Genero  Anio_de_nacimiento    Inicio_del_viaje  \
0  27598660       12551      M                1987 2023-03-01 00:00:32   
1  27598661     1153034      F                1994 2023-03-01 00:00:38   
2  27598668     1566425      M                1973 2023-03-01 00:04:52   
3  27598678      556440      M                2000 2023-03-01 00:05:55   
4  27598686      344644      M                2000 2023-03-01 00:07:33   

        Fin_del_viaje  Origen_Id  Destino_Id  
0 2023-03-01 00:11:09         80          39  
1 2023-03-01 00:09:47        188          17  
2 2023-03-01 00:20:43         86           4  
3 2023-03-01 00:18:36         85          85  
4 2023-03-01 00:18:54        241         198

Tenemos que hacer un parsing de los datos que no son enteros en este caso las caracteristicas que vamos a manejar que no son enteros son el Genero y el inicio del viaje. El genero es sencillo como designa un genero como 1 y al otros con el 0. Por otro lado, para el inicio de viaje una opcion seria pasar todo a UNIX time; sin embargo, esto no da mucha informacion a un clasificador y es una codificacion bastante burda.

Por la naturaleza de los datos uno puede intuir que se tienen ciertos patrones semanales e interesa mas analizar estos patrones para el clasificador que solo el UNIX time. Es decir, es posible que los tiempos de los lunes se parezcan mas que a los de otro lunes que a los del miercoles de la misma semana. Entonces, vamos tomar el *tiempos que ha pasado desde el inicio de semana*. Ademas de eso para tener una mejor agrupacion tomaremos intervalos de 15 minutos. Es decir, todos los Lunes de $0:00$ a $0:15$ seran identificados con la etiqueta $0$, los del $0:15$ asl $0:30$ con la etiqueta $1$ y asi sucesivamente. La funcion mostrada a continuacion hace justamente ese mapping de los tiempos.

In [3]:
def parse_datetime(dt):
    start_of_week = dt - datetime.timedelta(days=dt.weekday())
    start_of_week = start_of_week.replace(hour=0, minute=0, second=0)
    elapsed_time = dt - start_of_week
    minutes = elapsed_time.total_seconds()/60
    return int(minutes) // 15

def parseDF(df):
    df_copy = df.copy()
    # Make Gender a number
    df_copy["Genero"] = df_copy["Genero"].map(lambda x: x=='M')
    # Datetime to int
    df_copy["Inicio_del_viaje"] = df_copy["Inicio_del_viaje"].map(parse_datetime)
    return df_copy

parse_datetime(datetime.datetime.now())

660

En la siguiente celda dividimos nuestros datos en un conjunto de entrenamiento y uno de prueba para medir el rendimiento de los clasificadores.

In [4]:
features = ['Genero', 'Anio_de_nacimiento', 'Inicio_del_viaje', 'Origen_Id']

ParsedDF = parseDF(BiciDF[features + ['Destino_Id']])
# Standarize Features
ct = ColumnTransformer([
    ('std_features', StandardScaler(), features)
], remainder='passthrough')
stdData = ct.fit_transform(ParsedDF)

X_train, X_test, y_train, y_test = train_test_split(stdData[:, :-1],  stdData[:,-1], test_size=0.2)
print(f"We have {len(y_train)} samples for training and {len(y_test)} for Testing")

We have 319448 samples for training and 79862 for Testing


In [5]:
def check_classifier_and_cm(classifier, name):
    train_score = classifier.score(X_train, y_train)
    test_score  = classifier.score(X_test,  y_test)

    print(f"Training score: {train_score}")
    print(f"Test score: {test_score}")

    y_predicted = classifier.predict(X_test)
    cm = confusion_matrix(y_predicted, y_test)

    fig = go.Figure(data=go.Heatmap(z=cm))
    fig.update_layout(
        title=f"Matriz de confusion ({name})", 
        xaxis_title = "Clase Predicha",
        yaxis_title = "Clase Verdadera"
    )
    fig.show()

    good_traces = cm.diagonal()
    bad_traces  = np.sum(cm, axis = 1) - good_traces
    
    fig = go.Figure(data=[
        go.Bar(name='Predicciones Correctas',   y = good_traces),
        go.Bar(name='Predicciones Incorrectas', y = bad_traces)
    ])
    fig.update_layout(
        barmode = 'group', 
        xaxis_title = "Clase Predicha",
        title = f"Score de las predicciones ({name})"
    )
    fig.show()

    bad_traces  = np.sum(cm, axis = 0) - good_traces
    fig = go.Figure(data=[
        go.Bar(name='Predicciones Correctas',   y = good_traces),
        go.Bar(name='Predicciones Incorrectas', y = bad_traces)
    ])
    fig.update_layout(
        barmode='group', 
        xaxis_title = "Clase Verdadera",
        title = f"Score para cada clase ({name})"
    )
    fig.show()

# Clasificadores

## Red Neuronal

Como primer clasificador usaremos una red neuronal. En este caso, se eligio una configuracion $(16, 32, 64)$ para los perceptrones de las capas. Lamentablemente tenemos alrededor de 370 lugares para predicir y por lo tanto el entrenamiento es algo tardado.

In [6]:
NN = MLPClassifier(
    hidden_layer_sizes=(16, 32, 64), 
    random_state=1234, 
    #verbose=True, # Print classifier progress
    #max_iter=10 # Set max iteration to get results sooner
).fit(X_train, y_train)

check_classifier_and_cm(NN, "Red Neuronal")

c:\Users\joses\AppData\Local\Programs\Python\Python39\lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:686: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Training score: 0.0722402394129874
Test score: 0.0698580050587263


## Clasificador de Vecinos mas Cercanos

In [7]:
KNN = KNeighborsClassifier(n_neighbors = 15).fit(X_train, y_train)
check_classifier_and_cm(KNN, "K Vecinos mas Cercanos")

Training score: 0.21174338233452705
Test score: 0.09159550224136635


## Bosque Aleatorio

In [8]:
RandomForest = RandomForestClassifier(
    n_estimators=20,
    #verbose=True
).fit(X_train, y_train)
check_classifier_and_cm(RandomForest, "Bosque aleatorio")

Training score: 0.9022814354761964
Test score: 0.24677568806190678


## Arbol de Decisiones

In [9]:
DecisionTree = DecisionTreeClassifier().fit(X_train, y_train)
check_classifier_and_cm(DecisionTree, "Arbol de Decisiones")

Training score: 0.9090305777466129
Test score: 0.24492249129748817


## Analisis de Discriminante Cuadratico

In [10]:
QDA = QuadraticDiscriminantAnalysis().fit(X_train, y_train)
check_classifier_and_cm(QDA, "Analisis Discriminante Cuadratico")

Training score: 0.02994227542510831
Test score: 0.029776364228293807


## Gaussian Naive Bayes

In [11]:
GNB = GaussianNB().fit(X_train, y_train)
check_classifier_and_cm(GNB, "Gaussian Naive Bayes")

Training score: 0.02991723222558914
Test score: 0.0295259322331021


# Agrupacion de Lugares

Uno de los problemas que tienen los clasificadores que estamos usando es que tienen muchas clases sobre las cuales predecir (sin mencionar el desbalanceo de clases que se nos pidio dejarlo asi), por esta razon el siguiente paso que se puede realizar es intentar hacer un clasificador mas sencillo. 

Podemos dividir cada una de las localizaciones en `zonas` y podemos intentar predecir a que `zona` ira cada usuario en lugar de predecir el lugar exacto de llegada. Para esto usuaremos el algoritmo de agrupamiento aglomerada para crear esta clase de zonas.

In [12]:
LocationsDF = pd.read_csv("../data/nomenclatura_2023_02.csv", encoding = 'latin-1')
zonesDF = LocationsDF[["id", "latitude", "longitude"]]
zonesDF.head()

id   latitude   longitude
0   2  20.666378 -103.348820
1   3  20.667228 -103.366000
2   4  20.667690 -103.368252
3   5  20.691750 -103.362550
4   6  20.681151 -103.338863

In [13]:
coords = zonesDF[["latitude", "longitude"]].to_numpy()
clustering = AgglomerativeClustering(n_clusters=8).fit(coords)
zonesDF["zone"] = clustering.labels_
zonesDF.head()

C:\Users\joses\AppData\Local\Temp/ipykernel_3664/459432722.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



id   latitude   longitude  zone
0   2  20.666378 -103.348820     1
1   3  20.667228 -103.366000     1
2   4  20.667690 -103.368252     1
3   5  20.691750 -103.362550     6
4   6  20.681151 -103.338863     3

In [14]:
fig = px.scatter(zonesDF, x="latitude", y="longitude", color="zone")
fig.show()

In [15]:
ParsedDF2 = ParsedDF.merge(
    zonesDF, 
    left_on  = 'Destino_Id', 
    right_on = 'id', 
    how = 'left'
).drop(
    ['Destino_Id', 'id', 'latitude', 'longitude'],
    axis = 1
).rename(
    columns={'zone':'DestinoZone'}
).merge(
    zonesDF,
    left_on  = 'Origen_Id', 
    right_on = 'id', 
    how = 'left'
).drop(
    ['Origen_Id', 'id', 'latitude', 'longitude'],
    axis = 1
).rename(
    columns={'zone':'OriginalZone'}
)
ParsedDF2.head()

Genero  Anio_de_nacimiento  Inicio_del_viaje  DestinoZone  OriginalZone
0    True                1987               192            1             1
1   False                1994               192            2             2
2    True                1973               192            1             1
3    True                2000               192            1             1
4    True                2000               192            2             0

In [16]:
features = ['Genero', 'Anio_de_nacimiento', 'Inicio_del_viaje', 'OriginalZone']

# Standarize Features
ct = ColumnTransformer([
    ('std_features', StandardScaler(), features)
], remainder='passthrough')
stdData2 = ct.fit_transform(ParsedDF2)

X_train, X_test, y_train, y_test = train_test_split(stdData2[:, :-1],  stdData2[:,-1], test_size=0.2)
print(f"We have {len(y_train)} samples for training and {len(y_test)} for Testing")

We have 319448 samples for training and 79862 for Testing


## Red Neuronal

In [17]:
NN = MLPClassifier(
    hidden_layer_sizes=(16, 32, 64), 
    random_state=1234, 
    #verbose=True, # Print classifier progress
    #max_iter=10 # Set max iteration to get results sooner
).fit(X_train, y_train)

check_classifier_and_cm(NN, "Red Neuronal")

Training score: 0.564251458766372
Test score: 0.5666399539205129


## Clasificador de Vecinos mas Cercanos

In [18]:
KNN = KNeighborsClassifier(n_neighbors = 15).fit(X_train, y_train)
check_classifier_and_cm(KNN, "K Vecinos mas Cercanos")

Training score: 0.6084088803185494
Test score: 0.5688813202774786


## Bosque Aleatorio

In [19]:
RandomForest = RandomForestClassifier(
    n_estimators=20,
    #verbose=True
).fit(X_train, y_train)
check_classifier_and_cm(RandomForest, "Bosque aleatorio")

Training score: 0.7411691417695525
Test score: 0.5492599734542085


## Arbol de Decisiones

In [20]:
DecisionTree = DecisionTreeClassifier().fit(X_train, y_train)
check_classifier_and_cm(DecisionTree, "Arbol de Decisiones")

Training score: 0.7443496281084871
Test score: 0.5513135158147805


## Analisis de Discriminante Cuadratico

In [21]:
QDA = QuadraticDiscriminantAnalysis().fit(X_train, y_train)
check_classifier_and_cm(QDA, "Analisis Discriminante Cuadratico")

Training score: 0.49401154491497834
Test score: 0.49646890886779693


## Gaussian Naive Bayes

In [22]:
GNB = GaussianNB().fit(X_train, y_train)
check_classifier_and_cm(GNB, "Gaussian Naive Bayes")

Training score: 0.4950633592947835
Test score: 0.4974706368485638
